In [1]:
import pandas as pd
from ch2.data import *
from ch2.squeal.database import connect

s = session('-v 0')
raw = activity_statistics(s, SPEED, DISTANCE, ELEVATION, CADENCE, LATITUDE, LONGITUDE, HEART_RATE,
                         local_time='2018-03-04 12:00', activity_group_name='Bike', with_timespan=True)
raw.describe()

Timespan ID       Distance   Heart Rate    Elevation     Latitude  \
count   2933.000000    2933.000000  2933.000000  2784.000000  2885.000000   
mean   19834.102284   52424.331323   114.568360   580.671118   -33.473723   
std       29.722209   29499.017849    13.942284   149.218650     0.034321   
min    19783.000000       0.000000    65.000000   401.366177   -33.549516   
25%    19806.000000   29534.110000   105.000000   479.115404   -33.501597   
50%    19828.000000   52038.000000   115.000000   518.720135   -33.460546   
75%    19855.000000   79518.980000   125.000000   617.829422   -33.448303   
max    19892.000000  102708.060000   161.000000   997.497194   -33.420239   

           Cadence        Speed    Longitude  
count  2903.000000  2886.000000  2885.000000  
mean     61.558043     5.694779   -70.806271  
std      45.063903     2.914509     0.108272  
min       0.000000     0.000000   -70.949936  
25%       0.000000     3.154000   -70.922318  
50%      87.000000     6.196000   -70.826145  
75%     100.000000     7.539000   -70.706109  
max     159.000000    13.175000   -70.607797

In [2]:
from ch2.data.power import *

df = linear_resample(raw)
df = add_differentials(df)
df = add_energy_budget(df, m=64+12)
df = add_air_speed(df, 0, 0)
df = add_loss_estimate(df)
df = add_power_estimate(df)
print(measure_initial_scaling(df))
df = add_modeled_hr(df, 3600, 0.16, 15)


(0.08731667900389808, 110.41651226836042, 14.0)


In [3]:
model = fit_power(df, PowerModel(cda=0.45, slope=0.08, delay=14), 
                  'slope', 'delay')
print(model)

PowerModel(cda=0.45, crr=0, slope=0.1768799903075688, window=3600, delay=7.808516903594118, m=70, wind_speed=0, wind_heading=0)


In [4]:
df = add_modeled_hr(df, 3600, 0.177, 15)

In [5]:
from bokeh.plotting import output_notebook, show
from bokeh.layouts import row, column

from ch2.data.plot import *

output_notebook()
df['error'] = df[DETRENDED_HEART_RATE] - df[PREDICTED_HEART_RATE]
show(column([comparison_line_plot(700, 200, TIME, y, df) 
             for y in (POWER, HEART_RATE, DETRENDED_HEART_RATE, PREDICTED_HEART_RATE, 'error')]))


Loading BokehJS ...

In [6]:
print(1800 / median_dt(df))
df[HEART_RATE].rolling(360, center=True, min_periods=1).median()

257.14285714285717


2018-03-04 10:16:33+00:00    101.000000
2018-03-04 10:16:40+00:00    101.000000
2018-03-04 10:16:47+00:00    101.000000
2018-03-04 10:16:54+00:00    101.000000
2018-03-04 10:17:01+00:00    101.000000
2018-03-04 10:17:08+00:00    101.125000
2018-03-04 10:17:15+00:00    101.250000
2018-03-04 10:17:22+00:00    101.339286
2018-03-04 10:17:29+00:00    101.428571
2018-03-04 10:17:36+00:00    101.464286
2018-03-04 10:17:43+00:00    101.500000
2018-03-04 10:17:50+00:00    101.583333
2018-03-04 10:17:57+00:00    101.666667
2018-03-04 10:18:04+00:00    101.666667
2018-03-04 10:18:11+00:00    101.666667
2018-03-04 10:18:18+00:00    101.666667
2018-03-04 10:18:25+00:00    101.666667
2018-03-04 10:18:32+00:00    101.722222
2018-03-04 10:18:39+00:00    101.777778
2018-03-04 10:18:46+00:00    101.888889
2018-03-04 10:18:53+00:00    102.000000
2018-03-04 10:19:00+00:00    102.000000
2018-03-04 10:19:07+00:00    102.000000
2018-03-04 10:19:14+00:00    102.000000
2018-03-04 10:19:21+00:00    102.000000
